In [1]:
import pandas as pd
import requests
from shapely import wkt
from shapely.geometry import Polygon, LineString
import matplotlib.pyplot as plt
import contextily as cx
import geopandas as gpd
import numpy as np
from tqdm import tqdm
import os
import time
from contextlib import ContextDecorator
from multiprocessing import Process, Queue

In [2]:
gdf = gpd.read_file("work/data/stoej.json")
gdf_edges = gpd.read_file("work/data/edges.json")


#casting to new epsg in order to use meters in the buffer zone
gdf = gdf.to_crs(epsg=25832)
gdf_edges = gdf_edges.to_crs(epsg=25832)

In [3]:
class TimeoutException(Exception):
    pass

class ProcessWithTimeout(ContextDecorator):
    def __init__(self, seconds, queue):
        self.seconds = seconds
        self.queue = queue

    def __enter__(self):
        self.p = Process(target=self._target)
        self.p.start()

    def _target(self):
        try:
            result = self.queue.get(timeout=self.seconds)
            return result
        except TimeoutError:
            raise TimeoutException()

    def __exit__(self, *exc):
        self.p.terminate()

In [4]:
#Generate a spatial index to speed up the intersection method later on
lines_index = gdf_edges.sindex

In [5]:
def calculate_intersection_area(row, polygon):
    return row['geometry'].intersection(polygon).area


def find_top_matches(polygon, lines_df, buffer_dist=20, max_matches=3):
    buffered_poly = polygon.buffer(buffer_dist) 
    potential_matches_idx = list(lines_index.intersection(buffered_poly.bounds))
    potential_matches = lines_df.iloc[potential_matches_idx].copy()

    if not potential_matches.empty:
        potential_matches['intersect_area'] = potential_matches.apply(calculate_intersection_area, args=(polygon,), axis=1)
        sorted_matches = potential_matches.sort_values('intersect_area', ascending=False)
        top_matches = sorted_matches.head(max_matches)

        return top_matches

    return None



def find_top_matches_with_timeout(row, gdf_edges, queue):
    try:
        top_matches = find_top_matches(row['geometry'], gdf_edges)
        queue.put(top_matches)
    except Exception as e:
        queue.put(e)


#If it take more than <timeout> to process a polygon, the process is terminated and continues with the next polygon
def process_polygon(row, gdf_edges, timeout):
    queue = Queue()
    p = Process(target=find_top_matches_with_timeout, args=(row, gdf_edges, queue))
    p.start()
    p.join(timeout)
    
    if p.is_alive():
        p.terminate()
        p.join()
        raise TimeoutException("Timeout occurred during processing")
    
    result = queue.get()
    
    return result




In [6]:
results = []
counter = 0
for index, row in tqdm(gdf.iterrows(), total=len(gdf), desc="Processing polygons"): 
    # counter += 1    #for testing purposes
    # if counter > 300:
    #     break
    try:
        top_matches = process_polygon(row, gdf_edges, timeout=120)  

        if top_matches is not None:
            top_matches.loc[:, 'polygon_index'] = index
            isov1_value = row['isov1']
            isov2_value = row['isov2']
            top_matches.loc[:, 'isov1'] = isov1_value 
            top_matches.loc[:, 'isov2'] = isov2_value
            results.append(top_matches)

    except TimeoutException as e:
        print(f"Timeout occurred for polygon {row.name}: {e}")
print("Done!")

final_gdf = gpd.GeoDataFrame(pd.concat(results, ignore_index=True), crs="EPSG:25832")
#final_gdf = final_gdf.to_crs(epsg=2643)

final_gdf.to_file("work/data/noise_final.json", driver="GeoJSON")

Processing polygons:   5%|███▏                                                       | 197/3613 [00:11<02:26, 23.38it/s]

Timeout occurred for polygon 197: Timeout occurred during processing


Processing polygons:  20%|████████████                                               | 737/3613 [00:46<38:47,  1.24it/s]

Timeout occurred for polygon 736: Timeout occurred during processing


Processing polygons:  20%|████████████                                               | 739/3613 [00:49<53:43,  1.12s/it]

...

Timeout occurred for polygon 1618: Timeout occurred during processing


Processing polygons:  45%|██████████████████████████                                | 1624/3613 [03:16<32:43,  1.01it/s]

Timeout occurred for polygon 1623: Timeout occurred during processing


Processing polygons:  45%|██████████████████████████▏                               | 1634/3613 [03:17<03:59,  8.27it/s]Process Process-1635:

Traceback (most recent call last):
  File "/opt/conda/lib/python3.9/multiprocessing/process.py", line 315, in _bootstrap
    self.run()
  File "/opt/conda/lib/python3.9/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/tmp/ipykernel_29343/997730357.py", line 23, in find_top_matches_with_timeout
    top_matches = find_top_matches(row['geometry'], gdf_edges)
  File "/tmp/ipykernel_29343/997730357.py", line 11, in find_top_matches
    potential_matches['intersect_area'] = potential_matches.apply(calculate_intersection_area, args=(polygon,), axis=1)
  File "/opt/conda/lib/python3.9/site-packages/geopandas/geodataframe.py", line 1390, in apply
    result = super().apply(
  File "/opt/conda/lib/python3.9/site-packages/pandas/core/frame.py", line 8839, in apply
    return op.apply().__finalize__(self, 

KeyboardInterrupt: 

In [ ]:
final_gdf.explore()